# Assignment 5: Viterbi Decoding Algorithm

Rohaan Advani - 111903151

In [1]:
# Import Libraries
import numpy as np
import pandas as pd
import warnings
warnings.filterwarnings('ignore')

# Import Data and Extract Text and Tags
df = pd.read_csv('brown.csv')
df.drop(df.columns[0:4], axis = 1, inplace = True)
df.drop(df.columns[2], axis = 1, inplace = True)
for i in range(df.shape[0]):
    df['tokenized_text'][i] = df['tokenized_text'][i].split()
    df['tokenized_pos'][i] = df['tokenized_pos'][i].split()
df

tokenized_text  \
0      [Furthermore, ,, as, an, encouragement, to, re...   
1      [The, Unitarian, clergy, were, an, exclusive, ...   
2      [Ezra, Stiles, Gannett, ,, an, honorable, repr...   
3      [Even, so, ,, Gannett, judiciously, argued, ,,...   
4      [We, today, are, not, entitled, to, excoriate,...   
...                                                  ...   
57335  [For, the, most, part, ,, this, discussion, wi...   
57336                                             [A, .]   
57337  [Standard, preparations, and, units, of, thyro...   
57338  [The, international, unit, (, u., ), ,, adopte...   
57339  [The, international, unit, is, equipotent, wit...   

                                           tokenized_pos  
0      [rb, ,, cs, at, nn, in, nn, nn, ,, pps, rb, be...  
1      [at, jj, nns, bed, at, jj, nn, in, vbn, nns, -...  
2      [np, np, np, ,, at, jj, nn, in, at, nn, ,, vbd...  
3      [rb, rb, ,, np, rb, vbd, ,, at, nn-tl, md, rb,...  
4      [ppss, nr, ber, *, vbn, to, vb, jj, nns, wps, ...  
...                                                  ...  
57335  [in, at, ap, nn, ,, dt, nn, md, be, vbn, in, n...  
57336                                      [np-hl, .-hl]  
57337  [jj-hl, nns-hl, cc-hl, nns-hl, in-hl, jj-hl, n...  
57338  [at, jj, nn, (, nn, ), ,, vbn, to, vb, jj, at,...  
57339  [at, jj, nn, bez, jj, in, at, nn, nn, vbn, in,...  

[57340 rows x 2 columns]

In [2]:
# Build Word-Tag List of Corpus
wt = [] 
for i in range(df.shape[0]):
    for j in range(len(df['tokenized_text'][i])):
        tmp = []
        # Add start tag wherever sentence begins
        if j == 0:
            tmp.append('<st>')
            tmp.append('<st>')
            wt.append(tmp)
            tmp = []
        tmp.append(df['tokenized_text'][i][j])
        tmp.append(df['tokenized_pos'][i][j])
        wt.append(tmp)
        # Add ends tag wherever sentence finishes
        if j == len(df['tokenized_text'][i]) - 1:
            tmp = []
            tmp.append('</st>')
            tmp.append('</st>')
            wt.append(tmp)
wt

[['<st>', '<st>'],
 ['Furthermore', 'rb'],
 [',', ','],
 ['as', 'cs'],
 ['an', 'at'],
 ['encouragement', 'nn'],
 ['to', 'in'],
 ['revisionist', 'nn'],
 ['thinking', 'nn'],
 [',', ','],
 ['it', 'pps'],
 ['manifestly', 'rb'],
 ['is', 'bez'],
 ['fair', 'jj'],
 ['to', 'to'],
 ['admit', 'vb'],
 ['that', 'cs'],
 ['any', 'dti'],
 ['fraternity', 'nn'],
 ['has', 'hvz'],
 ['a', 'at'],
 ['constitutional', 'jj'],
 ['right', 'nn'],
 ['to', 'to'],
 ['refuse', 'vb'],
 ['to', 'to'],
 ['accept', 'vb'],
 ['persons', 'nns'],
 ['it', 'pps'],
 ['dislikes', 'vbz'],
 ['.', '.'],
 ['</st>', '</st>'],
 ['<st>', '<st>'],
 ['The', 'at'],
 ['Unitarian', 'jj'],
 ['clergy', 'nns'],
 ['were', 'bed'],
 ['an', 'at'],
 ['exclusive', 'jj'],
 ['club', 'nn'],
 ['of', 'in'],
 ['cultivated', 'vbn'],
 ['gentlemen', 'nns'],
 ['--', '--'],
 ['as', 'cs'],
 ['the', 'at'],
 ['term', 'nn'],
 ['was', 'bedz'],
 ['then', 'rb'],
 ['understood', 'vbn'],
 ['in', 'in'],
 ['the', 'at'],
 ['Back', 'jj-tl'],
 ['Bay', 'nn-tl'],
 ['--', '--']

In [3]:
# Ordered Tag List of Corpus
tag_list = [] 
for i in wt:
    tag_list.append(i[1])
# Create Tag-Freq List C(ti) or C(ti-1) for probability calculations
tag_freq = [[l, tag_list.count(l)] for l in set(tag_list)] 
print(tag_freq)

[['fw-od-nc', 1], ['ppl-tl', 1], ['uh-nc', 5], ['in-hl', 508], ['fw-at+np-tl', 2], ['ppss+ber', 278], ['vb', 33693], ['rb+bez-nc', 1], ['ap-nc', 2], ['fw-nps', 2], ['jj', 64015], ['nns$-hl', 4], ['nn+bez-tl', 2], ['active', 1], ['od', 1933], ['nps$-hl', 1], ['jj-tl-hl', 26], ['do', 1353], ['dod*', 402], ['fw-jjt', 1], ['jj+jj-nc', 2], ['hvz', 2433], ['chamber', 1], ['bed', 3282], ['lBOD', 1], ['hvd-hl', 1], ['rb-tl', 40], ['doz-tl', 2], ['at-tl-hl', 5], [',-tl', 4], ['ap$', 9], ['ppss', 13802], ['wrb-tl', 9], ['in-tl-hl', 6], ['fw-nn', 288], ['nn+in', 1], ['fw-in+at-t', 3], ['jjs-hl', 1], ['np-tl', 4016], ['sec', 3], ['ppo', 11181], ['be-tl', 1], ['dod*-tl', 1], ['vbd-nc', 11], ['vbn-nc', 9], ['fw-nns-tl', 36], ["64''", 3], ['jjr+cs', 1], ['nr$', 66], ['bez-hl', 30], ['(-hl', 162], ['ap-tl', 18], ['16', 2], ['20th', 1], ['od-hl', 8], ['or', 17], ['ppss+bez', 1], ['hv', 3928], ['dod-nc', 1], ['wdt', 5539], ['</st>', 57340], ['vbn', 29185], ['wps+bez-nc', 2], [':', 1558], ['wps-tl', 12],

In [4]:
# Tag Bigram List - Ordered set of bigrams as occuring in corpus
tag_bigrams = []
for i in range(len(tag_list) - 1):
    tmp = []
    tmp.append(tag_list[i])
    tmp.append(tag_list[i+1])
    tag_bigrams.append(tmp)
tag_bigrams

[['<st>', 'rb'],
 ['rb', ','],
 [',', 'cs'],
 ['cs', 'at'],
 ['at', 'nn'],
 ['nn', 'in'],
 ['in', 'nn'],
 ['nn', 'nn'],
 ['nn', ','],
 [',', 'pps'],
 ['pps', 'rb'],
 ['rb', 'bez'],
 ['bez', 'jj'],
 ['jj', 'to'],
 ['to', 'vb'],
 ['vb', 'cs'],
 ['cs', 'dti'],
 ['dti', 'nn'],
 ['nn', 'hvz'],
 ['hvz', 'at'],
 ['at', 'jj'],
 ['jj', 'nn'],
 ['nn', 'to'],
 ['to', 'vb'],
 ['vb', 'to'],
 ['to', 'vb'],
 ['vb', 'nns'],
 ['nns', 'pps'],
 ['pps', 'vbz'],
 ['vbz', '.'],
 ['.', '</st>'],
 ['</st>', '<st>'],
 ['<st>', 'at'],
 ['at', 'jj'],
 ['jj', 'nns'],
 ['nns', 'bed'],
 ['bed', 'at'],
 ['at', 'jj'],
 ['jj', 'nn'],
 ['nn', 'in'],
 ['in', 'vbn'],
 ['vbn', 'nns'],
 ['nns', '--'],
 ['--', 'cs'],
 ['cs', 'at'],
 ['at', 'nn'],
 ['nn', 'bedz'],
 ['bedz', 'rb'],
 ['rb', 'vbn'],
 ['vbn', 'in'],
 ['in', 'at'],
 ['at', 'jj-tl'],
 ['jj-tl', 'nn-tl'],
 ['nn-tl', '--'],
 ['--', 'cc'],
 ['cc', 'np'],
 ['np', 'bedz'],
 ['bedz', 'rb'],
 ['rb', '*'],
 ['*', 'at'],
 ['at', 'nn'],
 ['nn', ','],
 [',', 'cc'],
 ['cc', '

In [5]:
for i in range(len(tag_bigrams)):
    tag_bigrams[i] = ' '.join(tag_bigrams[i])

# Tag Bigram Freq List C(ti-1 ti) 
tag_bigram_freq = [] 
for l in set(tag_bigrams):
    cnt = tag_bigrams.count(l)
    x = l.split()
    x.append(cnt)
    tag_bigram_freq.append(x)
print(tag_bigram_freq)

[['rb', 'pps', 621], ['np-tl', 'rbr', 1], ['nn-tl', 'c', 3], ['fw-cc', 'fw-vbg', 1], ['bedz', 'pn$', 3], ['in', 'fw-ppl', 8], ['watt', ')', 1], ['nps-tl', 'bez', 1], [',-hl', 'nns-hl', 14], ['jj', 'uh', 2], ['qlp', 'ap', 1], ['at', "4''", 2], ['nn', 'fw-nn-tl', 1], ['bez', 'hvg', 2], ['vbn', 'od', 8], ['jjr', 'nr', 1], ['vbz-hl', 'np-hl', 5], ['jj-tl', ')', 10], ['rbr', ',', 158], ['rbt', 'pp$', 1], ['nn$', 'nr', 3], ['ex', 'hvd*', 2], ['in', 'pn-tl', 2], ['np-tl', 'ex', 1], ['rb', 'bez*', 4], ['``', '*', 54], ['at-nc', 'jjt-nc', 1], ['cs', 'jjs', 1], ['fw-nn', 'md', 2], ['cd', 'at', 94], ['vbd', ')', 4], ["'", ',', 21], ['bed', 'vbn', 1008], ['pn', 'pn', 2], ['fw-cd', 'vbn', 1], ['ppl', 'dt', 6], ['vbg', '*', 16], ['fw-nn$', "''", 1], ['``', 'vb-nc', 5], ['ppss', 'do', 214], ['od-tl', 'nn', 4], ['``', 'nns$-tl', 3], ['cc-hl', 'nps-hl', 2], ['dod*', ',', 3], ['wps+bez-tl', 'wps-tl', 1], ['nns$', '*', 1], ['nr', 'vbz', 9], ['jjr', 'abn', 2], ['vbn', 'pp$', 330], ['pps+bez-nc', 'jj-nc', 

In [6]:
# Tag Trans Prob = C(ti-1 ti) / C(ti-1)
tag_trans_prob = []
for l in tag_bigram_freq:
    tmp = []
    tmp.append(l[0])
    tmp.append(l[1])
    bigram_cnt = l[2]
    prev_tag = l[0]
    for j in tag_freq:
        if j[0] == prev_tag:
            prev_tag_cnt = j[1]
            break
    p = bigram_cnt / prev_tag_cnt
    tmp.append(p)
    tag_trans_prob.append(tmp)
print(tag_trans_prob)

[['rb', 'pps', 0.017030495831505045], ['np-tl', 'rbr', 0.000249003984063745], ['nn-tl', 'c', 0.0002243493867783428], ['fw-cc', 'fw-vbg', 0.037037037037037035], ['bedz', 'pn$', 0.00030593514174994904], ['in', 'fw-ppl', 6.636966242730448e-05], ['watt', ')', 1.0], ['nps-tl', 'bez', 0.014925373134328358], [',-hl', 'nns-hl', 0.08187134502923976], ['jj', 'uh', 3.124267749746153e-05], ['qlp', 'ap', 0.0038314176245210726], ['at', "4''", 2.0416704947988444e-05], ['nn', 'fw-nn-tl', 6.5619811933619e-06], ['bez', 'hvg', 0.00019868865487780648], ['vbn', 'od', 0.0002741134144252184], ['jjr', 'nr', 0.0005107252298263534], ['vbz-hl', 'np-hl', 0.06944444444444445], ['jj-tl', ')', 0.0024372410431391664], ['rbr', ',', 0.13367174280879865], ['rbt', 'pp$', 0.009900990099009901], ['nn$', 'nr', 0.002027027027027027], ['ex', 'hvd*', 0.0009242144177449168], ['in', 'pn-tl', 1.659241560682612e-05], ['np-tl', 'ex', 0.000249003984063745], ['rb', 'bez*', 0.00010969723562966213], ['``', '*', 0.006110671042208894], [

In [7]:
for i in range(len(wt)):
    wt[i] = ' '.join(wt[i])

# Word tag freq list C(ti, wi)
word_tag_freq = [] 
for l in set(wt):
    cnt = wt.count(l)
    x = l.split()
    x.append(cnt)
    word_tag_freq.append(x)
print(word_tag_freq)

[['boards', 'vbz', 1], ['Chiang', 'np', 4], ['rapid-transit', 'nn', 1], ['Welsh', 'jj', 4], ['Kaisers', 'nps', 1], ['McClellan', 'np', 12], ['ma', 'nn', 1], ['Happy', 'jj-tl', 3], ['privacy', 'nn', 11], ['principles', 'nns-hl', 1], ["More's", 'np$', 7], ['Hetman', 'np', 12], ['jury', 'nn', 62], ['woeful', 'jj', 1], ['198', 'cd-tl', 1], ['dilates', 'vbz', 1], ['mascara', 'nn', 1], ['cartridges', 'nns', 5], ['epitomized', 'vbn', 2], ['Merc', 'np', 1], ['courteously', 'rb', 3], ['permits', 'vbz', 25], ['societies', 'nns', 38], ['consign', 'vb', 2], ['Long-term', 'nn', 1], ["sitter's", 'nn$', 2], ['bastards', 'nns', 12], ['Burgundies', 'nps', 1], ['snakestrike', 'nn', 1], ['short', 'rb', 14], ['playful', 'jj', 3], ['Wheaton', 'np', 2], ['glisten', 'nn', 2], ['catapults', 'vbz', 1], ['flag-stick', 'nn', 1], ['Burger', 'np', 1], ['speeds', 'nns-hl', 1], ['banks', 'vbz', 1], ['$14,000', 'nns', 1], ['Alex', 'np', 30], ['microwave', 'nn', 2], ['walker', 'nn', 1], ['well-designed', 'jj', 2], ['t

In [8]:
# Word Emis Prob = C(ti, wi) / C(ti)
word_emission_prob = []
for l in word_tag_freq:
    tmp = []
    tmp.append(l[0])
    tmp.append(l[1])
    wt_cnt = l[2]
    tag = l[1]
    for j in tag_freq:
        if j[0] == tag:
            tag_cnt = j[1]
            break
    p = wt_cnt / tag_cnt
    tmp.append(p)
    word_emission_prob.append(tmp)
print(word_emission_prob)

[['boards', 'vbz', 0.0001356300013563], ['Chiang', 'np', 0.00011602274045712959], ['rapid-transit', 'nn', 6.5619811933619e-06], ['Welsh', 'jj', 6.248535499492306e-05], ['Kaisers', 'nps', 0.000784313725490196], ['McClellan', 'np', 0.0003480682213713888], ['ma', 'nn', 6.5619811933619e-06], ['Happy', 'jj-tl', 0.00073117231294175], ['privacy', 'nn', 7.21817931269809e-05], ['principles', 'nns-hl', 0.0016420361247947454], ["More's", 'np$', 0.0027290448343079924], ['Hetman', 'np', 0.0003480682213713888], ['jury', 'nn', 0.0004068428339884378], ['woeful', 'jj', 1.5621338748730765e-05], ['198', 'cd-tl', 0.0011160714285714285], ['dilates', 'vbz', 0.0001356300013563], ['mascara', 'nn', 6.5619811933619e-06], ['cartridges', 'nns', 9.07490425976006e-05], ['epitomized', 'vbn', 6.85283536063046e-05], ['Merc', 'np', 2.9005685114282398e-05], ['courteously', 'rb', 8.22729267222466e-05], ['permits', 'vbz', 0.0033907500339075], ['societies', 'nns', 0.0006896927237417645], ['consign', 'vb', 5.935951087763036

In [9]:
# Function sorts nested list by the ith element in sub list
def Sort(l, i):
    l.sort(key = lambda x: x[i])
    return l

# Function takes string input along with the calculated tag trans and work emis prob lists
# Function returns list of most probable tag sequence
def viterbi(inp, ttp, wep):
    x = inp.split()
    init_tag = '<st>'
    prev_p = 1
    pos = []
    for i in x:
        next_tag = []
        for j in ttp:
            if j[0] == init_tag:
                next_tag.append([j[1], j[2]])
        l = next_tag
        for j in next_tag:
            for k in wep:
                if i == k[0] and j[0] == k[1]:
                    j.append(k[2])
                    break
            if len(j) == 3:
                j.append(j[1]*j[2]*prev_p)
        next_tag = [i for i in next_tag if len(i) == 4]
        next_tag = Sort(next_tag, 3)
        l2 = next_tag
        ans = next_tag[-1:][0]
        l3 = ans
        pos.append(ans[0])
        init_tag = ans[0]
        prev_p = ans[3]
    return pos

In [10]:
test = 'The international Police Branch'
pos = viterbi(test, tag_trans_prob, word_emission_prob)
print(pos)

['at', 'jj', 'nns', 'nn']


In [11]:
test_cases = []
test_inp = ['The international Police Branch', 'Atkinson has blue-eyes', 'U.S. cops', 'Arctic cabins , Beyond Eastwick']
for i in test_inp:
    test_cases.append(i)
    pos = viterbi(i, tag_trans_prob, word_emission_prob)
    test_cases.append(', '.join(pos))

In [12]:
with open("111903151_A5_TTP.txt", "w") as f:
    for i in tag_trans_prob:
        f.write(' '.join(str(i)))
        f.write('\n')
    
with open("111903151_A5_WEP.txt", "w") as f:
    for i in word_emission_prob:
        f.write(' '.join(str(i)))
        f.write('\n')
    
with open("111903151_A5_Output.txt", "w") as f:
    for i in test_cases:
        f.write(' '.join(str(i)))
        f.write('\n')